[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/sebascarag/AI-SyntheticSound/blob/main/optuna-urbansound8k-vae.ipynb)

https://siddhartha01writes.medium.com/gpu-t4-vs-gpu-p100-kaggle-gpu-cd852d56022c

TPU P100 Should be used for training and for Inference both GPUT P100 for GPUT T4 can be used.

In [3]:
!wget https://raw.githubusercontent.com/sebascarag/AI-SyntheticSound/main/Model_CVAE.ipynb

--2023-12-13 04:05:25--  https://raw.githubusercontent.com/sebascarag/AI-SyntheticSound/main/Model_CVAE.ipynb
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 11397 (11K) [text/plain]
Saving to: ‘Model_CVAE.ipynb’

Model_CVAE.ipynb    100%[===================>]  11.13K  --.-KB/s    in 0s      

2023-12-13 04:05:26 (111 MB/s) - ‘Model_CVAE.ipynb’ saved [11397/11397]



In [4]:
!pip install optuna
import optuna

import h5py
import time
from torch.utils.data import TensorDataset
from sklearn import preprocessing
import numpy as np
import torch
from torch.utils.data import DataLoader

!pip install import-ipynb
import import_ipynb

from google.colab import files
import os

if not os.path.exists("/content/Model_CVAE.ipynb"): files.upload()
import Model_CVAE as m_cvae

importing Jupyter notebook from Model_CVAE.ipynb


In [6]:
from importlib import reload
reload(m_cvae)

importing Jupyter notebook from Model_CVAE.ipynb


<module 'Model_CVAE' from 'Model_CVAE.ipynb'>

## Dataset

In [7]:
!wget https://github.com/sebascarag/AI-SyntheticSound/raw/main/Resources/vggish_features_labels.hdf5

--2023-12-13 04:06:00--  https://github.com/sebascarag/AI-SyntheticSound/raw/main/Resources/vggish_features_labels.hdf5
Resolving github.com (github.com)... 140.82.114.3
Connecting to github.com (github.com)|140.82.114.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/sebascarag/AI-SyntheticSound/main/Resources/vggish_features_labels.hdf5 [following]
--2023-12-13 04:06:00--  https://raw.githubusercontent.com/sebascarag/AI-SyntheticSound/main/Resources/vggish_features_labels.hdf5
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 29046056 (28M) [application/octet-stream]
Saving to: ‘vggish_features_labels.hdf5’

vggish_features_lab 100%[===================>]  27.70M  --.-KB/s    in 0.1s    

2023-1

In [8]:
with h5py.File('/content/vggish_features_labels.hdf5', 'r') as f:
  data_file = np.array(f.get("data")).astype(float)
print(data_file.shape)
print(type(data_file))
print(data_file[0][0])
print(min(data_file[0]))
print(max(data_file[0]))

(7077, 513)
<class 'numpy.ndarray'>
166.0
0.0
255.0


In [9]:
scaler = preprocessing.MinMaxScaler(feature_range=(0, 1))
features = scaler.fit_transform(data_file[:,:-1])
print("features", features.shape)
print("features", type(features))
print("value",features[0][0])
print("min", min(features[0]))
print("max",max(features[0]))
labels = data_file[:,-1].astype(int)
print("labels", labels.shape)
print("labels", labels[0])

features (7077, 512)
features <class 'numpy.ndarray'>
value 0.4285714285714286
min 0.0
max 1.0
labels (7077,)
labels 2


In [10]:
dataset = TensorDataset( torch.Tensor(features), torch.Tensor(labels) )
x, y = next(enumerate(dataset))
print(x, y)

0 (tensor([0.4286, 0.5763, 0.5957, 0.7378, 1.0000, 0.2713, 0.3596, 0.8250, 1.0000,
        0.4333, 0.4627, 0.3020, 1.0000, 0.5765, 0.0000, 0.0549, 0.6353, 0.2745,
        0.7961, 0.6745, 0.0353, 0.8480, 0.4039, 0.6863, 0.8314, 0.0000, 0.8784,
        0.7686, 0.6706, 0.4667, 0.9059, 0.6314, 0.1294, 0.4549, 0.0510, 0.3843,
        0.6196, 0.8784, 0.9725, 0.6431, 0.2314, 1.0000, 0.6392, 0.0392, 0.3843,
        0.2784, 0.0235, 0.0863, 0.7451, 1.0000, 0.1686, 0.4588, 1.0000, 1.0000,
        0.0000, 0.2000, 0.2471, 0.0000, 0.0000, 0.7961, 0.6000, 0.0000, 0.2784,
        0.5843, 0.9529, 0.9333, 0.7961, 0.6863, 1.0000, 0.6392, 0.1647, 1.0000,
        0.9686, 0.0000, 0.6353, 0.0000, 0.1804, 0.0000, 0.7647, 1.0000, 0.8667,
        1.0000, 0.4235, 0.0000, 0.0000, 1.0000, 1.0000, 1.0000, 0.9176, 0.4235,
        0.0000, 0.0000, 1.0000, 1.0000, 0.6392, 1.0000, 0.9059, 0.0000, 1.0000,
        0.7765, 0.6824, 0.2275, 0.0000, 0.2902, 1.0000, 1.0000, 1.0000, 1.0000,
        1.0000, 1.0000, 1.0000, 1.000

In [11]:
!nvidia-smi -L

GPU 0: Tesla T4 (UUID: GPU-94672164-541a-7389-8228-b3eaf1975522)


In [12]:
!lscpu

Architecture:            x86_64
  CPU op-mode(s):        32-bit, 64-bit
  Address sizes:         46 bits physical, 48 bits virtual
  Byte Order:            Little Endian
CPU(s):                  2
  On-line CPU(s) list:   0,1
Vendor ID:               GenuineIntel
  Model name:            Intel(R) Xeon(R) CPU @ 2.30GHz
    CPU family:          6
    Model:               63
    Thread(s) per core:  2
    Core(s) per socket:  1
    Socket(s):           1
    Stepping:            0
    BogoMIPS:            4599.99
    Flags:               fpu vme de pse tsc msr pae mce cx8 apic sep mtrr pge mca cmov pat pse36 clf
                         lush mmx fxsr sse sse2 ss ht syscall nx pdpe1gb rdtscp lm constant_tsc rep_
                         good nopl xtopology nonstop_tsc cpuid tsc_known_freq pni pclmulqdq ssse3 fm
                         a cx16 pcid sse4_1 sse4_2 x2apic movbe popcnt aes xsave avx f16c rdrand hyp
                         ervisor lahf_lm abm invpcid_single ssbd ibrs ibpb stibp

## Optimize v1 - Exploration
* latent_dims=[3-203]
* num_hidden_layers=[150-400]
* learning_rate=[1e-5-1e-2]
* num_epochs=[20-100]
* data scale [0-1]
* batch_size = 12

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
# torch.cuda.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 12, shuffle = False)

def create_model(trial):
  params = {
    'latent_dims': trial.suggest_int('latent_dims', 3, 203),
    'num_features': 512,
    'num_hidden_layers': trial.suggest_int('num_hidden_layers', 150, 400),
    'num_classes': 10,
    'random_seed': random_seed
  }
  modelCVAE = m_cvae.ConditionalVariationalAutoencoder(**params).to(device)
  return modelCVAE

def objective(trial):
  model = create_model(trial)
  # <ipython-input-10-6b59815d81c9>:31: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0.
  # See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead. 'learning_rate': trial.suggest_loguniform('learning_rate', 1e-5, 1e-2),
  params = {
    'data': data,
    'learning_rate': trial.suggest_float('learning_rate', 1e-5, 1e-2, log=True),
    'num_epochs': trial.suggest_int('num_epochs', 20, 100),
    'kl_version': 2,
    'optuna_trial': trial
  }
  best_model, best_loss, losses = model.train_fit(**params)
  return best_loss

study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner( # MedianPruner: se centra en los resultados anteriores y elimina las combinaciones que se encuentren por debajo de la mediana de los resultados obtenidos hasta ese momento.
        #n_startup_trials=2, # ignorando los resultados de las dos primeras pruebas
        n_warmup_steps=5, # nro de pruebas antes de comenzar a aplicar la poda.
        interval_steps=3 # intervalo de pasos entre las aplicaciones de la poda
    ), direction="minimize")

# n_jobs: pruebas paralelas
study.optimize(objective, n_trials=100, n_jobs=4)

print(study.best_trial.value)
print(study.best_params)

[I 2023-08-14 19:14:48,869] A new study created in memory with name: no-name-dce601ac-1960-4caf-ae01-40c2d57a55ce


Device: cuda:0
Device: cuda:0
Device: cuda:0
Device: cuda:0
Epoch: 001/020 | Batch 000/589 | kl: 31.8121 + pw: 4371.9033 = loss: 4403.7153 | KL v02
Epoch: 001/047 | Batch 000/589 | kl: 2.6296 + pw: 4372.2100 = loss: 4374.8394 | KL v02
Epoch: 001/053 | Batch 000/589 | kl: 44.9106 + pw: 4392.6641 = loss: 4437.5747 | KL v02
Epoch: 001/077 | Batch 000/589 | kl: 7.6470 + pw: 4379.4863 = loss: 4387.1333 | KL v02
Epoch: 001/020 | Batch 020/589 | kl: 20.3231 + pw: 4381.3628 = loss: 4401.6860 | KL v02
Epoch: 001/020 | Batch 040/589 | kl: 12.7927 + pw: 4375.7041 = loss: 4388.4971 | KL v02
Epoch: 001/020 | Batch 060/589 | kl: 10.4894 + pw: 4371.5239 = loss: 4382.0132 | KL v02
Epoch: 001/053 | Batch 053/589 | kl: 12.9320 + pw: 4349.1406 = loss: 4362.0728 | KL v02
Epoch: 001/047 | Batch 047/589 | kl: 16.6005 + pw: 3953.9663 = loss: 3970.5667 | KL v02
Epoch: 001/020 | Batch 080/589 | kl: 10.8115 + pw: 4361.6143 = loss: 4372.4258 | KL v02
Epoch: 001/020 | Batch 100/589 | kl: 7.8867 + pw: 4356.5156 = 

[I 2023-08-14 19:16:58,094] Trial 0 finished with value: 3857.1957076767744 and parameters: {'latent_dims': 182, 'num_hidden_layers': 171, 'learning_rate': 1.4542018293372599e-05, 'num_epochs': 20}. Best is trial 0 with value: 3857.1957076767744.


Epoch: 020/020 | Batch 580/589 | kl: 27.4864 + pw: 3863.3340 = loss: 3890.8203 | KL v02
Time elapsed: 0.18 min
Epoch: 012/077 | Batch 000/589 | kl: 87.6066 + pw: 3324.8223 = loss: 3412.4287 | KL v02
Time elapsed: 0.10 min
Total Training Time: 2.10 min
Device: cuda:0
Epoch: 001/060 | Batch 000/589 | kl: 32.0204 + pw: 4393.8945 = loss: 4425.9150 | KL v02
Epoch: 019/053 | Batch 159/589 | kl: 39.2743 + pw: 3790.5293 = loss: 3829.8035 | KL v02
Epoch: 017/047 | Batch 141/589 | kl: 52.4858 + pw: 3426.1182 = loss: 3478.6040 | KL v02
Epoch: 001/060 | Batch 060/589 | kl: 23.8778 + pw: 4059.4512 = loss: 4083.3289 | KL v02
Epoch: 019/053 | Batch 212/589 | kl: 34.9544 + pw: 3937.1377 = loss: 3972.0920 | KL v02
Epoch: 017/047 | Batch 188/589 | kl: 63.3435 + pw: 3524.1057 = loss: 3587.4492 | KL v02
Epoch: 001/060 | Batch 120/589 | kl: 33.2987 + pw: 3803.8354 = loss: 3837.1343 | KL v02
Epoch: 019/053 | Batch 265/589 | kl: 49.6823 + pw: 3574.1362 = loss: 3623.8186 | KL v02
Epoch: 017/047 | Batch 235/58

[I 2023-08-14 19:20:54,869] Trial 1 finished with value: 3456.169431524762 and parameters: {'latent_dims': 18, 'num_hidden_layers': 301, 'learning_rate': 0.002490353998361843, 'num_epochs': 47}. Best is trial 1 with value: 3456.169431524762.


...

Time elapsed: 0.09 min
Total Training Time: 5.87 min
Epoch: 012/072 | Batch 072/589 | kl: 94.9303 + pw: 3435.1982 = loss: 3530.1287 | KL v02
Epoch: 042/063 | Batch 378/589 | kl: 78.0447 + pw: 3372.4441 = loss: 3450.4888 | KL v02
Epoch: 012/072 | Batch 144/589 | kl: 104.9101 + pw: 3394.3486 = loss: 3499.2588 | KL v02
Epoch: 042/063 | Batch 441/589 | kl: 99.5668 + pw: 3252.7061 = loss: 3352.2729 | KL v02
Epoch: 012/072 | Batch 216/589 | kl: 81.6815 + pw: 3371.6929 = loss: 3453.3743 | KL v02
Epoch: 042/063 | Batch 504/589 | kl: 69.3229 + pw: 3494.5732 = loss: 3563.8962 | KL v02
Epoch: 012/072 | Batch 288/589 | kl: 68.8772 + pw: 3507.8037 = loss: 3576.6809 | KL v02
Epoch: 042/063 | Batch 567/589 | kl: 89.9776 + pw: 3459.1936 = loss: 3549.1711 | KL v02


[I 2023-08-14 20:53:08,160] Trial 97 pruned. 


Time elapsed: 0.09 min
Prune on epoch: 041 | loss:3394.7551
Epoch: 012/072 | Batch 360/589 | kl: 56.5487 + pw: 3980.0591 = loss: 4036.6077 | KL v02
Epoch: 012/072 | Batch 432/589 | kl: 67.6527 + pw: 3604.4756 = loss: 3672.1284 | KL v02
Epoch: 012/072 | Batch 504/589 | kl: 64.6158 + pw: 3580.9329 = loss: 3645.5488 | KL v02
Epoch: 012/072 | Batch 576/589 | kl: 76.3788 + pw: 3447.7766 = loss: 3524.1555 | KL v02
Time elapsed: 0.05 min
Epoch: 013/072 | Batch 000/589 | kl: 100.3476 + pw: 3222.2993 = loss: 3322.6470 | KL v02
Epoch: 013/072 | Batch 072/589 | kl: 92.5013 + pw: 3446.1763 = loss: 3538.6775 | KL v02
Epoch: 013/072 | Batch 144/589 | kl: 104.0918 + pw: 3441.9084 = loss: 3546.0002 | KL v02
Epoch: 013/072 | Batch 216/589 | kl: 84.1427 + pw: 3352.4148 = loss: 3436.5576 | KL v02
Epoch: 013/072 | Batch 288/589 | kl: 64.6463 + pw: 3511.2737 = loss: 3575.9199 | KL v02
Epoch: 013/072 | Batch 360/589 | kl: 64.3319 + pw: 3977.6052 = loss: 4041.9373 | KL v02
Epoch: 013/072 | Batch 432/589 | kl

[I 2023-08-14 20:54:53,802] Trial 99 finished with value: 3362.2569518008477 and parameters: {'latent_dims': 8, 'num_hidden_layers': 382, 'learning_rate': 0.0004926495798061809, 'num_epochs': 72}. Best is trial 17 with value: 3351.246394994703.


Epoch: 072/072 | Batch 576/589 | kl: 93.4291 + pw: 3376.6157 = loss: 3470.0449 | KL v02
Time elapsed: 0.03 min
Total Training Time: 2.93 min
3351.246394994703
{'latent_dims': 20, 'num_hidden_layers': 357, 'learning_rate': 0.000670453058929, 'num_epochs': 98}


## Results v1

In [ ]:
prunedTrials = len(study.get_trials(states=[optuna.trial.TrialState.PRUNED]))
completeTrials = len(study.get_trials(states=[optuna.trial.TrialState.COMPLETE]))
print("* Pruned trials: ", prunedTrials)
print("* Complete trials: ", completeTrials)
print("* %: ", (completeTrials / (prunedTrials + completeTrials))*100 )
print("* Best Score: ", study.best_trial.value)
print("* Best Params by key: ", study.best_params)

* Pruned trials:  68
* Complete trials:  32
* %:  32.0
* Best Score:  3351.246394994703
* Best Params by key:  {'latent_dims': 20, 'num_hidden_layers': 357, 'learning_rate': 0.000670453058929, 'num_epochs': 98}


In [ ]:
df_best = study.trials_dataframe().sort_values(by="value")
df_best = df_best[df_best.state == "COMPLETE"]
df_best

number        value             datetime_start          datetime_complete  \
17      17  3351.246395 2023-08-14 19:31:29.855963 2023-08-14 19:44:04.110425   
18      18  3359.953422 2023-08-14 19:32:46.742629 2023-08-14 19:42:10.346271   
92      92  3361.356400 2023-08-14 20:40:40.567847 2023-08-14 20:49:10.516476   
99      99  3362.256952 2023-08-14 20:51:58.083403 2023-08-14 20:54:53.801995   
70      70  3368.374825 2023-08-14 20:22:31.456638 2023-08-14 20:28:49.455857   
52      52  3371.429259 2023-08-14 20:12:11.366565 2023-08-14 20:24:59.913228   
96      96  3373.160850 2023-08-14 20:47:14.542860 2023-08-14 20:53:06.626506   
3        3  3373.210951 2023-08-14 19:14:48.884444 2023-08-14 19:29:36.363825   
81      81  3373.251318 2023-08-14 20:26:30.831293 2023-08-14 20:34:18.621151   
84      84  3373.683108 2023-08-14 20:33:13.980390 2023-08-14 20:39:58.555881   
80      80  3374.462602 2023-08-14 20:26:24.703840 2023-08-14 20:33:13.973498   
93      93  3374.737843 2023-08-14 20:41:13.659107 2023-08-14 20:47:14.536297   
94      94  3375.359183 2023-08-14 20:41:28.917536 2023-08-14 20:52:24.877164   
83      83  3375.800143 2023-08-14 20:29:27.762188 2023-08-14 20:35:32.892933   
85      85  3376.580187 2023-08-14 20:34:18.627098 2023-08-14 20:41:33.427311   
86      86  3377.362831 2023-08-14 20:35:32.900102 2023-08-14 20:41:13.652084   
36      36  3380.368146 2023-08-14 19:55:06.227306 2023-08-14 20:02:12.131011   
37      37  3382.361890 2023-08-14 19:58:20.486216 2023-08-14 20:05:51.358952   
46      46  3387.405734 2023-08-14 20:05:51.363650 2023-08-14 20:12:23.839911   
53      53  3397.010265 2023-08-14 20:12:21.374108 2023-08-14 20:16:32.868702   
55      55  3400.133254 2023-08-14 20:12:29.125377 2023-08-14 20:17:14.753904   
14      14  3418.381926 2023-08-14 19:26:51.649949 2023-08-14 19:31:29.847465   
66      66  3419.106252 2023-08-14 20:19:40.360441 2023-08-14 20:22:55.415175   
15      15  3427.414884 2023-08-14 19:29:02.651072 2023-08-14 19:32:46.736842   
11      11  3445.674248 2023-08-14 19:25:18.959682 2023-08-14 19:29:02.645263   
6        6  3447.214598 2023-08-14 19:20:56.092123 2023-08-14 19:24:41.245622   
1        1  3456.169432 2023-08-14 19:14:48.879691 2023-08-14 19:20:54.868821   
45      45  3457.288587 2023-08-14 20:04:15.817032 2023-08-14 20:06:34.188174   
4        4  3506.487667 2023-08-14 19:16:58.106108 2023-08-14 19:23:09.153668   
5        5  3553.098289 2023-08-14 19:20:54.874815 2023-08-14 19:24:31.623371   
2        2  3665.534298 2023-08-14 19:14:48.882380 2023-08-14 19:20:56.088281   
0        0  3857.195708 2023-08-14 19:14:48.874389 2023-08-14 19:16:58.093998   

                 duration  params_latent_dims  params_learning_rate  \
17 0 days 00:12:34.254462                  20              0.000670   
18 0 days 00:09:23.603642                   6              0.000819   
92 0 days 00:08:29.948629                  15              0.000610   
99 0 days 00:02:55.718592                   8              0.000493   
70 0 days 00:06:17.999219                  14              0.000723   
52 0 days 00:12:48.546663                  40              0.000451   
96 0 days 00:05:52.083646                  15              0.000475   
3  0 days 00:14:47.479381                  42              0.000313   
81 0 days 00:07:47.789858                  20              0.000514   
84 0 days 00:06:44.575491                  16              0.000551   
80 0 days 00:06:49.269658                  20              0.000491   
93 0 days 00:06:00.877190                  17              0.000451   
94 0 days 00:10:55.959628                  16              0.000598   
83 0 days 00:06:05.130745                  16              0.000549   
85 0 days 00:07:14.800213                  26              0.000605   
86 0 days 00:05:40.751982                  27              0.000671   
36 0 days 00:07:05.903705                  22              0.000773   
37 0 days 00:07:30.872736                  20       

In [ ]:
if completeTrials > 20:
    df_best = df_best.head(20).describe()
else:
    df_best = df_best.describe()
df_best

number        value                   duration  params_latent_dims  \
count  20.000000    20.000000                         20            20.00000   
mean   65.250000  3373.468615  0 days 00:07:47.476814750            19.10000   
std    30.050615     9.975911  0 days 00:02:58.131916791             9.18752   
min     3.000000  3351.246395     0 days 00:02:55.718592             6.00000   
25%    43.750000  3370.665651  0 days 00:06:04.067356250            14.75000   
50%    80.500000  3374.072855  0 days 00:06:57.586681500            16.50000   
75%    87.500000  3376.775848  0 days 00:08:43.362382250            20.50000   
max    99.000000  3397.010265     0 days 00:14:47.479381            42.00000   

       params_learning_rate  params_num_epochs  params_num_hidden_layers  
count             20.000000          20.000000                   20.0000  
mean               0.000587          63.150000                  361.9000  
std                0.000146          13.596729                   31.5993  
min                0.000313          40.000000                  286.0000  
25%                0.000487          57.000000                  356.0000  
50%                0.000569          58.500000                  373.0000  
75%                0.000671          67.500000                  383.2500  
max                0.000929          98.000000                  394.0000

In [ ]:
optuna.visualization.plot_slice(study)

In [ ]:
optuna.visualization.plot_param_importances(study)

In [ ]:
optuna.visualization.plot_optimization_history(study)

In [ ]:
optuna.visualization.plot_contour(study)

In [ ]:
optuna.visualization.plot_rank(study)

In [ ]:
optuna.visualization.plot_intermediate_values(study)

In [ ]:
optuna.visualization.plot_timeline(study)

## Optimize v2 - Exploration
* latent_dims=[6-50]
* num_hidden_layers=[300-450]
* learning_rate=[3e-4-9.3e-4]
* num_epochs=[40-150]
* data scale [0-1]
* batch_size = 12

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
# torch.cuda.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 12, shuffle = False)

def create_model(trial):
  params = {
    'latent_dims': trial.suggest_int('latent_dims', 6, 50),
    'num_features': 512,
    'num_hidden_layers': trial.suggest_int('num_hidden_layers', 300, 450),
    'num_classes': 10,
    'random_seed': random_seed
  }
  modelCVAE = m_cvae.ConditionalVariationalAutoencoder(**params).to(device)
  return modelCVAE

def objective(trial):
  model = create_model(trial)
  # <ipython-input-10-6b59815d81c9>:31: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0.
  # See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead. 'learning_rate': trial.suggest_loguniform('learning_rate', 1e-5, 1e-2),
  params = {
    'data': data,
    'learning_rate': trial.suggest_float('learning_rate', 3e-4, 9.3e-4, log=True),
    'num_epochs': trial.suggest_int('num_epochs', 40, 150),
    'kl_version': 2,
    'optuna_trial': trial
  }
  best_model, best_loss, losses = model.train_fit(**params)
  return best_loss

study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner( # MedianPruner: se centra en los resultados anteriores y elimina las combinaciones que se encuentren por debajo de la mediana de los resultados obtenidos hasta ese momento.
        #n_startup_trials=2, # ignorando los resultados de las dos primeras pruebas
        n_warmup_steps=5, # nro de pruebas antes de comenzar a aplicar la poda.
        interval_steps=3 # intervalo de pasos entre las aplicaciones de la poda
    ), direction="minimize")

# n_jobs: pruebas paralelas
study.optimize(objective, n_trials=100, n_jobs=4)

print(study.best_trial.value)
print(study.best_params)

[I 2023-08-14 21:05:00,364] A new study created in memory with name: no-name-8353c53a-5a91-427e-91b4-9eff61bf0497


Device: cuda:0
Device: cuda:0
Device: cuda:0
Device: cuda:0
Epoch: 001/044 | Batch 000/589 | kl: 9.9807 + pw: 4367.7158 = loss: 4377.6963 | KL v02
Epoch: 001/087 | Batch 000/589 | kl: 3.3159 + pw: 4360.5342 = loss: 4363.8501 | KL v02
Epoch: 001/118 | Batch 000/589 | kl: 7.7588 + pw: 4377.2983 = loss: 4385.0571 | KL v02
Epoch: 001/087 | Batch 000/589 | kl: 6.7569 + pw: 4372.4102 = loss: 4379.1670 | KL v02
Epoch: 001/044 | Batch 044/589 | kl: 1.7315 + pw: 4166.7520 = loss: 4168.4834 | KL v02
Epoch: 001/087 | Batch 087/589 | kl: 2.6862 + pw: 3925.6292 = loss: 3928.3154 | KL v02
Epoch: 001/044 | Batch 088/589 | kl: 0.8824 + pw: 3812.1260 = loss: 3813.0083 | KL v02
Epoch: 001/087 | Batch 087/589 | kl: 1.4157 + pw: 3937.1313 = loss: 3938.5471 | KL v02
Epoch: 001/118 | Batch 118/589 | kl: 2.2320 + pw: 3962.9365 = loss: 3965.1685 | KL v02
Epoch: 001/044 | Batch 132/589 | kl: 2.0059 + pw: 3659.5056 = loss: 3661.5115 | KL v02
Epoch: 001/087 | Batch 174/589 | kl: 8.2938 + pw: 3914.3782 = loss: 39

[I 2023-08-14 21:10:04,440] Trial 1 finished with value: 3407.0095686573095 and parameters: {'latent_dims': 45, 'num_hidden_layers': 312, 'learning_rate': 0.0009006300634358305, 'num_epochs': 44}. Best is trial 1 with value: 3407.0095686573095.


Epoch: 044/044 | Batch 572/589 | kl: 116.2220 + pw: 3261.7476 = loss: 3377.9695 | KL v02
Time elapsed: 0.11 min
Total Training Time: 5.07 min
Device: cuda:0
Epoch: 001/057 | Batch 000/589 | kl: 6.2759 + pw: 4384.9326 = loss: 4391.2085 | KL v02
Epoch: 049/087 | Batch 348/589 | kl: 105.9241 + pw: 3349.0957 = loss: 3455.0198 | KL v02
Epoch: 027/087 | Batch 087/589 | kl: 99.0033 + pw: 3359.4219 = loss: 3458.4250 | KL v02
Time elapsed: 0.14 min
Epoch: 040/118 | Batch 000/589 | kl: 101.5584 + pw: 3137.5732 = loss: 3239.1316 | KL v02
Epoch: 001/057 | Batch 057/589 | kl: 6.3677 + pw: 3833.2600 = loss: 3839.6277 | KL v02
Epoch: 049/087 | Batch 435/589 | kl: 87.4534 + pw: 3367.6477 = loss: 3455.1011 | KL v02
Epoch: 001/057 | Batch 114/589 | kl: 5.4461 + pw: 4015.3044 = loss: 4020.7505 | KL v02
Epoch: 027/087 | Batch 174/589 | kl: 102.4180 + pw: 3033.6685 = loss: 3136.0864 | KL v02
Epoch: 040/118 | Batch 118/589 | kl: 90.1637 + pw: 3656.2524 = loss: 3746.4160 | KL v02
Epoch: 049/087 | Batch 522/5

[I 2023-08-14 21:14:06,373] Trial 0 finished with value: 3360.951298083289 and parameters: {'latent_dims': 14, 'num_hidden_layers': 308, 'learning_rate': 0.0005823670376665886, 'num_epochs': 87}. Best is trial 0 with value: 3360.951298083289.


...

Time elapsed: 0.09 min
Prune on epoch: 080 | loss:3351.4137
Epoch: 076/087 | Batch 435/589 | kl: 113.0444 + pw: 3281.3179 = loss: 3394.3623 | KL v02
Epoch: 041/096 | Batch 096/589 | kl: 99.8016 + pw: 3446.5161 = loss: 3546.3176 | KL v02
Epoch: 076/087 | Batch 522/589 | kl: 116.1617 + pw: 3282.7764 = loss: 3398.9380 | KL v02
Time elapsed: 0.09 min
Epoch: 077/087 | Batch 000/589 | kl: 105.5822 + pw: 3137.8208 = loss: 3243.4031 | KL v02
Epoch: 041/096 | Batch 192/589 | kl: 99.9681 + pw: 3519.5872 = loss: 3619.5552 | KL v02
Epoch: 077/087 | Batch 087/589 | kl: 104.3177 + pw: 3319.9019 = loss: 3424.2195 | KL v02
Epoch: 041/096 | Batch 288/589 | kl: 79.7537 + pw: 3492.1196 = loss: 3571.8733 | KL v02
Epoch: 077/087 | Batch 174/589 | kl: 120.2480 + pw: 2952.1309 = loss: 3072.3789 | KL v02
Epoch: 041/096 | Batch 384/589 | kl: 97.4919 + pw: 3301.6396 = loss: 3399.1316 | KL v02
Epoch: 077/087 | Batch 261/589 | kl: 103.9157 + pw: 3239.1450 = loss: 3343.0608 | KL v02
Epoch: 041/096 | Batch 480/589 

[I 2023-08-14 23:53:18,045] Trial 95 pruned. 


Epoch: 043/096 | Batch 000/589 | kl: 100.0596 + pw: 3162.5132 = loss: 3262.5728 | KL v02
Time elapsed: 0.06 min
Prune on epoch: 077 | loss:3352.7432
Epoch: 043/096 | Batch 096/589 | kl: 100.4358 + pw: 3422.7000 = loss: 3523.1357 | KL v02
Epoch: 043/096 | Batch 192/589 | kl: 103.5044 + pw: 3491.2329 = loss: 3594.7373 | KL v02
Epoch: 043/096 | Batch 288/589 | kl: 76.4075 + pw: 3473.9121 = loss: 3550.3196 | KL v02
Epoch: 043/096 | Batch 384/589 | kl: 93.9430 + pw: 3295.4385 = loss: 3389.3813 | KL v02
Epoch: 043/096 | Batch 480/589 | kl: 111.7381 + pw: 2996.2227 = loss: 3107.9607 | KL v02
Epoch: 043/096 | Batch 576/589 | kl: 87.1593 + pw: 3432.3545 = loss: 3519.5139 | KL v02
Time elapsed: 0.03 min
Epoch: 044/096 | Batch 000/589 | kl: 106.3189 + pw: 3152.5854 = loss: 3258.9043 | KL v02
Epoch: 044/096 | Batch 096/589 | kl: 98.1941 + pw: 3432.5205 = loss: 3530.7146 | KL v02
Epoch: 044/096 | Batch 192/589 | kl: 96.9472 + pw: 3502.3154 = loss: 3599.2627 | KL v02
Epoch: 044/096 | Batch 288/589 |

[I 2023-08-14 23:54:46,984] Trial 99 pruned. 


Epoch: 093/096 | Batch 576/589 | kl: 100.2576 + pw: 3362.6292 = loss: 3462.8867 | KL v02
Time elapsed: 0.03 min
Prune on epoch: 092 | loss:3345.2501
3325.7206220206567
{'latent_dims': 12, 'num_hidden_layers': 439, 'learning_rate': 0.0005971347134205606, 'num_epochs': 144}


## Results v2

In [ ]:
prunedTrials = len(study.get_trials(states=[optuna.trial.TrialState.PRUNED]))
completeTrials = len(study.get_trials(states=[optuna.trial.TrialState.COMPLETE]))
print("* Pruned trials: ", prunedTrials)
print("* Complete trials: ", completeTrials)
print("* %: ", (completeTrials / (prunedTrials + completeTrials)) * 100)
print("* Best Score: ", study.best_trial.value)
print("* Best Params by key: ", study.best_params)

* Pruned trials:  75
* Complete trials:  25
* %:  25.0
* Best Score:  3325.7206220206567
* Best Params by key:  {'latent_dims': 12, 'num_hidden_layers': 439, 'learning_rate': 0.0005971347134205606, 'num_epochs': 144}


In [ ]:
df_best = study.trials_dataframe().sort_values(by="value")
df_best = df_best[df_best.state == "COMPLETE"]
df_best

number        value             datetime_start          datetime_complete  \
38      38  3325.720622 2023-08-14 22:12:26.551970 2023-08-14 22:31:13.054688   
33      33  3326.851865 2023-08-14 21:53:46.298750 2023-08-14 22:12:26.548195   
10      10  3330.867631 2023-08-14 21:21:30.215703 2023-08-14 21:38:16.633977   
62      62  3338.745352 2023-08-14 23:02:18.272143 2023-08-14 23:12:50.451843   
54      54  3338.758211 2023-08-14 22:50:13.098063 2023-08-14 23:02:04.967899   
56      56  3339.520871 2023-08-14 22:51:40.825708 2023-08-14 23:02:18.262846   
32      32  3339.577488 2023-08-14 21:53:16.716814 2023-08-14 22:04:40.356505   
65      65  3343.300618 2023-08-14 23:09:18.845169 2023-08-14 23:20:00.914135   
2        2  3344.834257 2023-08-14 21:05:00.374944 2023-08-14 21:20:19.556380   
37      37  3345.859758 2023-08-14 22:09:26.330512 2023-08-14 22:18:45.098669   
35      35  3346.573054 2023-08-14 22:00:00.740039 2023-08-14 22:09:26.324727   
74      74  3347.555932 2023-08-14 23:25:20.117234 2023-08-14 23:34:09.393266   
29      29  3347.759222 2023-08-14 21:49:40.465933 2023-08-14 22:00:00.725640   
34      34  3348.006612 2023-08-14 21:55:10.207705 2023-08-14 22:12:27.299954   
25      25  3348.637788 2023-08-14 21:39:50.474779 2023-08-14 21:52:11.592044   
26      26  3358.519661 2023-08-14 21:39:58.955921 2023-08-14 21:48:06.062014   
27      27  3359.640067 2023-08-14 21:40:20.955582 2023-08-14 21:55:10.202231   
3        3  3359.666255 2023-08-14 21:05:00.378058 2023-08-14 21:21:46.308733   
0        0  3360.951298 2023-08-14 21:05:00.369091 2023-08-14 21:14:06.373143   
12      12  3366.332568 2023-08-14 21:22:55.376800 2023-08-14 21:36:21.908811   
5        5  3370.673224 2023-08-14 21:14:06.379957 2023-08-14 21:20:48.765735   
4        4  3376.668458 2023-08-14 21:10:04.445563 2023-08-14 21:16:39.269207   
67      67  3377.599070 2023-08-14 23:13:33.578117 2023-08-14 23:23:07.340395   
68      68  3380.844058 2023-08-14 23:14:53.645598 2023-08-14 23:20:46.024761   
1        1  3407.009569 2023-08-14 21:05:00.372378 2023-08-14 21:10:04.439701   

                 duration  params_latent_dims  params_learning_rate  \
38 0 days 00:18:46.502718                  12              0.000597   
33 0 days 00:18:40.249445                  17              0.000569   
10 0 days 00:16:46.418274                  37              0.000610   
62 0 days 00:10:32.179700                   7              0.000647   
54 0 days 00:11:51.869836                  11              0.000570   
56 0 days 00:10:37.437138                  12              0.000569   
32 0 days 00:11:23.639691                  15              0.000586   
65 0 days 00:10:42.068966                  10              0.000581   
2  0 days 00:15:19.181436                  35              0.000303   
37 0 days 00:09:18.768157                  14              0.000557   
35 0 days 00:09:25.584688                  15              0.000555   
74 0 days 00:08:49.276032                  15              0.000618   
29 0 days 00:10:20.259707                  27              0.000550   
34 0 days 00:17:17.092249                  13              0.000588   
25 0 days 00:12:21.117265                  26              0.000665   
26 0 days 00:08:07.106093                  27              0.000527   
27 0 days 00:14:49.246649                  27              0.000536   
3  0 days 00:16:45.930675                  25              0.000665   
0  0 days 00:09:06.004052                  14              0.000582   
12 0 days 00:13:26.532011                   7              0.000506   
5  0 days 00:06:42.385778                  48              0.000624   
4  0 days 00:06:34.823644                  32              0.000339   
67 0 days 00:09:33.762278                  12              0.000539   
68 0 days 00:05:52.379163                  10              0.000604   
1  0 days 00:05:04.067323                  45              0.000901   

    params_num_epochs  params_num_hidden_layers   

In [ ]:
if completeTrials > 20:
    df_best = df_best.head(20).describe()
else:
    df_best = df_best.describe()
df_best

number        value                   duration  params_latent_dims  \
count  20.000000    20.000000                         20           20.000000   
mean   32.700000  3345.883957  0 days 00:12:43.323239100           18.300000   
std    21.332209    11.208392  0 days 00:03:29.154293973            8.933085   
min     0.000000  3325.720622     0 days 00:08:07.106093            7.000000   
25%    21.750000  3339.330206  0 days 00:10:06.590952250           12.000000   
50%    32.500000  3346.216406  0 days 00:11:37.754763500           15.000000   
75%    42.000000  3351.108257  0 days 00:15:40.868745750           26.250000   
max    74.000000  3366.332568     0 days 00:18:46.502718           37.000000   

       params_learning_rate  params_num_epochs  params_num_hidden_layers  
count             20.000000          20.000000                  20.00000  
mean               0.000569          99.300000                 413.75000  
std                0.000076          21.865859                  39.28556  
min                0.000303          70.000000                 308.00000  
25%                0.000554          87.000000                 396.00000  
50%                0.000575          93.500000                 434.00000  
75%                0.000600         102.250000                 444.25000  
max                0.000665         145.000000                 447.00000

In [ ]:
optuna.visualization.plot_slice(study)

In [ ]:
optuna.visualization.plot_param_importances(study)

In [ ]:
optuna.visualization.plot_optimization_history(study)

In [ ]:
optuna.visualization.plot_contour(study)

In [ ]:
optuna.visualization.plot_rank(study)

In [ ]:
optuna.visualization.plot_intermediate_values(study)

In [ ]:
optuna.visualization.plot_timeline(study)

## Optimize v3
* latent_dims=[7-30]
* num_hidden_layers=[400-490]
* learning_rate=[5e-4-7e-4]
* num_epochs=[100-200]
* data scale [0-1]
* batch_size = 12

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
# torch.cuda.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 12, shuffle = False)

def create_model(trial):
  params = {
    'latent_dims': trial.suggest_int('latent_dims', 7, 30),
    'num_features': 512,
    'num_hidden_layers': trial.suggest_int('num_hidden_layers', 400, 490),
    'num_classes': 10,
    'random_seed': random_seed
  }
  modelCVAE = m_cvae.ConditionalVariationalAutoencoder(**params).to(device)
  return modelCVAE

def objective(trial):
  model = create_model(trial)
  # <ipython-input-10-6b59815d81c9>:31: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0.
  # See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead. 'learning_rate': trial.suggest_loguniform('learning_rate', 1e-5, 1e-2),
  params = {
    'data': data,
    'learning_rate': trial.suggest_float('learning_rate', 5e-4, 7e-4, log=True),
    'num_epochs': trial.suggest_int('num_epochs', 100, 200),
    'kl_version': 2,
    'optuna_trial': trial
  }
  best_model, best_loss, losses = model.train_fit(**params)
  return best_loss

study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner( # MedianPruner: se centra en los resultados anteriores y elimina las combinaciones que se encuentren por debajo de la mediana de los resultados obtenidos hasta ese momento.
        #n_startup_trials=2, # ignorando los resultados de las dos primeras pruebas
        n_warmup_steps=5, # nro de pruebas antes de comenzar a aplicar la poda.
        interval_steps=3 # intervalo de pasos entre las aplicaciones de la poda
    ), direction="minimize")

# n_jobs: pruebas paralelas
study.optimize(objective, n_trials=100, n_jobs=4)

print(study.best_trial.value)
print(study.best_params)

[I 2023-08-15 15:43:52,342] A new study created in memory with name: no-name-bf575716-f0b3-4d59-885b-7413f7e287a9


Device: cuda:0
Device: cuda:0
Device: cuda:0
Device: cuda:0
Epoch: 001/144 | Batch 000/589 | kl: 1.9203 + pw: 4373.5977 = loss: 4375.5181 | KL v02Epoch: 001/135 | Batch 000/589 | kl: 2.1912 + pw: 4379.9375 = loss: 4382.1289 | KL v02
Epoch: 001/161 | Batch 000/589 | kl: 4.6719 + pw: 4382.6582 = loss: 4387.3301 | KL v02
Epoch: 001/176 | Batch 000/589 | kl: 4.2179 + pw: 4374.0273 = loss: 4378.2451 | KL v02

Epoch: 001/135 | Batch 135/589 | kl: 8.0136 + pw: 4007.7759 = loss: 4015.7896 | KL v02
Epoch: 001/161 | Batch 161/589 | kl: 15.3111 + pw: 3807.6831 = loss: 3822.9941 | KL v02
Epoch: 001/176 | Batch 176/589 | kl: 12.7422 + pw: 4081.5405 = loss: 4094.2827 | KL v02
Epoch: 001/144 | Batch 144/589 | kl: 3.4857 + pw: 3958.9568 = loss: 3962.4426 | KL v02
Epoch: 001/135 | Batch 270/589 | kl: 25.6123 + pw: 3776.7373 = loss: 3802.3496 | KL v02
Epoch: 001/161 | Batch 322/589 | kl: 38.8065 + pw: 3391.5188 = loss: 3430.3254 | KL v02
Epoch: 001/176 | Batch 352/589 | kl: 9.3333 + pw: 3811.7029 = loss

[I 2023-08-15 15:57:34,481] Trial 0 finished with value: 3328.112881521451 and parameters: {'latent_dims': 12, 'num_hidden_layers': 446, 'learning_rate': 0.0006116067324564813, 'num_epochs': 135}. Best is trial 0 with value: 3328.112881521451.


Time elapsed: 0.10 min
Total Training Time: 13.65 min
Device: cuda:0
Epoch: 001/146 | Batch 000/589 | kl: 5.4094 + pw: 4378.4468 = loss: 4383.8560 | KL v02
Epoch: 072/144 | Batch 576/589 | kl: 100.9876 + pw: 3368.8296 = loss: 3469.8171 | KL v02
Epoch: 123/176 | Batch 176/589 | kl: 155.1159 + pw: 3079.4934 = loss: 3234.6094 | KL v02
Epoch: 108/161 | Batch 483/589 | kl: 108.4858 + pw: 3269.2549 = loss: 3377.7407 | KL v02
Time elapsed: 0.19 min
Epoch: 073/144 | Batch 000/589 | kl: 100.5887 + pw: 3117.3689 = loss: 3217.9575 | KL v02
Epoch: 001/146 | Batch 146/589 | kl: 17.9152 + pw: 3985.2439 = loss: 4003.1592 | KL v02
Time elapsed: 0.13 min
Epoch: 109/161 | Batch 000/589 | kl: 109.2985 + pw: 3110.0391 = loss: 3219.3376 | KL v02
Epoch: 123/176 | Batch 352/589 | kl: 134.7656 + pw: 3087.1106 = loss: 3221.8762 | KL v02
Epoch: 001/146 | Batch 292/589 | kl: 36.6820 + pw: 3867.6091 = loss: 3904.2910 | KL v02
Epoch: 073/144 | Batch 144/589 | kl: 124.2545 + pw: 3200.2344 = loss: 3324.4890 | KL v02

[I 2023-08-15 16:03:36,563] Trial 1 finished with value: 3319.835852671478 and parameters: {'latent_dims': 22, 'num_hidden_layers': 464, 'learning_rate': 0.0006108895746807161, 'num_epochs': 176}. Best is trial 1 with value: 3319.835852671478.


...

Time elapsed: 0.11 min
Prune on epoch: 005 | loss:3558.5030
Epoch: 001/132 | Batch 264/589 | kl: 11.0228 + pw: 3787.7041 = loss: 3798.7268 | KL v02
Epoch: 010/186 | Batch 372/589 | kl: 66.0375 + pw: 3488.7349 = loss: 3554.7725 | KL v02
Epoch: 001/132 | Batch 396/589 | kl: 43.5216 + pw: 3817.0107 = loss: 3860.5322 | KL v02
Epoch: 010/186 | Batch 558/589 | kl: 92.7949 + pw: 3542.0386 = loss: 3634.8335 | KL v02
Epoch: 001/132 | Batch 528/589 | kl: 38.4988 + pw: 3942.1628 = loss: 3980.6616 | KL v02
Time elapsed: 0.13 min
Epoch: 011/186 | Batch 000/589 | kl: 83.3465 + pw: 3252.9734 = loss: 3336.3198 | KL v02
Time elapsed: 0.07 min
Epoch: 002/132 | Batch 000/589 | kl: 65.7046 + pw: 3565.4958 = loss: 3631.2004 | KL v02
Epoch: 002/132 | Batch 132/589 | kl: 64.5508 + pw: 3356.7595 = loss: 3421.3103 | KL v02
Epoch: 011/186 | Batch 186/589 | kl: 81.8185 + pw: 3335.7336 = loss: 3417.5522 | KL v02
Epoch: 002/132 | Batch 264/589 | kl: 37.7582 + pw: 3707.5659 = loss: 3745.3240 | KL v02
Epoch: 011/186

[I 2023-08-15 17:36:39,668] Trial 99 pruned. 


Time elapsed: 0.06 min
Prune on epoch: 005 | loss:3559.5323
Epoch: 015/186 | Batch 372/589 | kl: 88.6034 + pw: 3486.9272 = loss: 3575.5308 | KL v02
Epoch: 015/186 | Batch 558/589 | kl: 91.5543 + pw: 3501.9707 = loss: 3593.5249 | KL v02
Time elapsed: 0.05 min
Epoch: 016/186 | Batch 000/589 | kl: 85.1869 + pw: 3185.3093 = loss: 3270.4963 | KL v02
Epoch: 016/186 | Batch 186/589 | kl: 88.9825 + pw: 3324.1802 = loss: 3413.1626 | KL v02
Epoch: 016/186 | Batch 372/589 | kl: 84.3327 + pw: 3470.8374 = loss: 3555.1702 | KL v02
Epoch: 016/186 | Batch 558/589 | kl: 99.2446 + pw: 3483.0854 = loss: 3582.3301 | KL v02
Time elapsed: 0.03 min
Epoch: 017/186 | Batch 000/589 | kl: 77.1613 + pw: 3239.4666 = loss: 3316.6279 | KL v02
Epoch: 017/186 | Batch 186/589 | kl: 91.5940 + pw: 3304.0571 = loss: 3395.6511 | KL v02
Epoch: 017/186 | Batch 372/589 | kl: 72.6436 + pw: 3470.0830 = loss: 3542.7266 | KL v02
Epoch: 017/186 | Batch 558/589 | kl: 102.7411 + pw: 3472.2529 = loss: 3574.9941 | KL v02
Time elapsed:

[I 2023-08-15 17:37:01,354] Trial 94 pruned. 


Epoch: 027/186 | Batch 558/589 | kl: 113.5668 + pw: 3437.0664 = loss: 3550.6331 | KL v02
Time elapsed: 0.03 min
Prune on epoch: 026 | loss:3415.6399
3313.3579581567797
{'latent_dims': 8, 'num_hidden_layers': 490, 'learning_rate': 0.0006786873927231535, 'num_epochs': 180}


## Results v3

In [ ]:
prunedTrials = len(study.get_trials(states=[optuna.trial.TrialState.PRUNED]))
completeTrials = len(study.get_trials(states=[optuna.trial.TrialState.COMPLETE]))
print("* Pruned trials: ", prunedTrials)
print("* Complete trials: ", completeTrials)
print("* %: ", (completeTrials / (prunedTrials + completeTrials)) * 100)
print("* Best Score: ", study.best_trial.value)
print("* Best Params by key: ", study.best_params)

* Pruned trials:  89
* Complete trials:  11
* %:  11.0
* Best Score:  3313.3579581567797
* Best Params by key:  {'latent_dims': 8, 'num_hidden_layers': 490, 'learning_rate': 0.0006786873927231535, 'num_epochs': 180}


In [ ]:
df_best = study.trials_dataframe().sort_values(by="value")
df_best = df_best[df_best.state == "COMPLETE"]
df_best

number        value             datetime_start          datetime_complete  \
12      12  3313.357958 2023-08-15 16:14:34.841496 2023-08-15 16:32:57.214350   
1        1  3319.835853 2023-08-15 15:43:52.349321 2023-08-15 16:03:36.562633   
3        3  3322.199952 2023-08-15 15:43:52.356150 2023-08-15 16:04:18.726502   
4        4  3324.129734 2023-08-15 15:57:34.489310 2023-08-15 16:12:26.780743   
76      76  3325.346930 2023-08-15 17:18:00.981845 2023-08-15 17:32:36.510322   
67      67  3326.076139 2023-08-15 17:14:38.843830 2023-08-15 17:28:50.354149   
54      54  3326.935261 2023-08-15 17:01:47.605837 2023-08-15 17:15:31.757133   
0        0  3328.112882 2023-08-15 15:43:52.347813 2023-08-15 15:57:34.480407   
22      22  3328.493372 2023-08-15 16:21:51.737922 2023-08-15 16:38:14.724608   
2        2  3329.012943 2023-08-15 15:43:52.354818 2023-08-15 16:11:10.114398   
7        7  3335.225780 2023-08-15 16:11:10.119652 2023-08-15 16:31:11.837069   

                 duration  params_latent_dims  params_learning_rate  \
12 0 days 00:18:22.372854                   8              0.000679   
1  0 days 00:19:44.213312                  22              0.000611   
3  0 days 00:20:26.370352                  17              0.000695   
4  0 days 00:14:52.291433                  20              0.000609   
76 0 days 00:14:35.528477                  13              0.000641   
67 0 days 00:14:11.510319                  11              0.000590   
54 0 days 00:13:44.151296                  16              0.000629   
0  0 days 00:13:42.132594                  12              0.000612   
22 0 days 00:16:22.986686                  15              0.000631   
2  0 days 00:27:17.759580                  10              0.000544   
7  0 days 00:20:01.717417                  17              0.000576   

    params_num_epochs  params_num_hidden_layers     state  
12                180                       490  COMPLETE  
1                 176                       464  COMPLETE  
3                 161                       466  COMPLETE  
4                 146                       458  COMPLETE  
76                141                       487  COMPLETE  
67                125                       484  COMPLETE  
54                133                       487  COMPLETE  
0                 135                       446  COMPLETE  
22                129                       488  COMPLETE  
2                 144                       402  COMPLETE  
7                 105                       480  COMPLETE

In [ ]:
if completeTrials > 20:
    df_best = df_best.head(20).describe()
else:
    df_best = df_best.describe()
df_best

number        value                   duration  params_latent_dims  \
count  11.000000    11.000000                         11           11.000000   
mean   22.545455  3325.338800  0 days 00:17:34.639483636           14.636364   
std    28.804040     5.631414  0 days 00:04:09.446946183            4.295875   
min     0.000000  3313.357958     0 days 00:13:42.132594            8.000000   
25%     2.500000  3323.164843     0 days 00:14:23.519398           11.500000   
50%     7.000000  3326.076139     0 days 00:16:22.986686           15.000000   
75%    38.000000  3328.303127  0 days 00:19:52.965364500           17.000000   
max    76.000000  3335.225780     0 days 00:27:17.759580           22.000000   

       params_learning_rate  params_num_epochs  params_num_hidden_layers  
count             11.000000          11.000000                 11.000000  
mean               0.000620         143.181818                468.363636  
std                0.000043          22.189268                 26.390425  
min                0.000544         105.000000                402.000000  
25%                0.000599         131.000000                461.000000  
50%                0.000612         141.000000                480.000000  
75%                0.000636         153.500000                487.000000  
max                0.000695         180.000000                490.000000

In [ ]:
optuna.visualization.plot_slice(study)

In [ ]:
optuna.visualization.plot_param_importances(study)

In [ ]:
optuna.visualization.plot_optimization_history(study)

In [ ]:
optuna.visualization.plot_contour(study)

In [ ]:
optuna.visualization.plot_rank(study)

In [ ]:
optuna.visualization.plot_intermediate_values(study)

In [ ]:
optuna.visualization.plot_timeline(study)

## Best params with batch size 8 - Refining

* Best Score:  3313.3579581567797
* Best Params by key:  {'latent_dims': 8, 'num_hidden_layers': 490, 'learning_rate': 0.0006786873927231535, 'num_epochs': 180}

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 8, shuffle = False)

params = {
    'latent_dims': 8,
    'num_features': 512,
    'num_hidden_layers': 490,
    'num_classes': 10,
    'random_seed': random_seed
}
modelCVAE = m_cvae.ConditionalVariationalAutoencoder(**params).to(device)

params = {
    'data': data,
    'learning_rate': 0.0006786873927231535,
    'num_epochs': 180,
    'kl_version': 2
}
best_model, best_loss, losses = modelCVAE.train_fit(**params)

print(best_loss)

Device: cuda:0
Epoch: 001/180 | Batch 000/884 | kl: 0.4527 + pw: 2911.7241 = loss: 2912.1768 | KL v02
Epoch: 001/180 | Batch 180/884 | kl: 2.1875 + pw: 2492.7866 = loss: 2494.9741 | KL v02
Epoch: 001/180 | Batch 360/884 | kl: 6.7393 + pw: 2612.1611 = loss: 2618.9004 | KL v02
Epoch: 001/180 | Batch 540/884 | kl: 12.9934 + pw: 2973.9768 = loss: 2986.9702 | KL v02
Epoch: 001/180 | Batch 720/884 | kl: 8.5911 + pw: 2230.0127 = loss: 2238.6038 | KL v02
Time elapsed: 0.04 min
Epoch: 002/180 | Batch 000/884 | kl: 9.2077 + pw: 2502.9683 = loss: 2512.1760 | KL v02
Epoch: 002/180 | Batch 180/884 | kl: 23.7749 + pw: 2347.8499 = loss: 2371.6248 | KL v02
Epoch: 002/180 | Batch 360/884 | kl: 26.5783 + pw: 2393.7812 = loss: 2420.3596 | KL v02
Epoch: 002/180 | Batch 540/884 | kl: 22.7316 + pw: 2946.8230 = loss: 2969.5547 | KL v02
Epoch: 002/180 | Batch 720/884 | kl: 52.4874 + pw: 1996.5046 = loss: 2048.9919 | KL v02
Time elapsed: 0.04 min
Epoch: 003/180 | Batch 000/884 | kl: 16.3048 + pw: 2492.5425 = l

## Best params with batch size 4 - Explotation
* Best Score:  3313.3579581567797
* Best Params by key:  {'latent_dims': 8, 'num_hidden_layers': 490, 'learning_rate': 0.0006786873927231535, 'num_epochs': 180}

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 4, shuffle = False)

params = {
    'latent_dims': 8,
    'num_features': 512,
    'num_hidden_layers': 490,
    'num_classes': 10,
    'random_seed': random_seed
}
modelCVAE = m_cvae.ConditionalVariationalAutoencoder(**params).to(device)

params = {
    'data': data,
    'learning_rate': 0.0006786873927231535,
    'num_epochs': 180,
    'kl_version': 2
}
best_model, best_loss, losses = modelCVAE.train_fit(**params)

print(best_loss)

Device: cuda:0
Epoch: 001/180 | Batch 000/1769 | kl: 0.2283 + pw: 1455.3892 = loss: 1455.6174 | KL v02
Epoch: 001/180 | Batch 180/1769 | kl: 1.2557 + pw: 1370.9519 = loss: 1372.2076 | KL v02
Epoch: 001/180 | Batch 360/1769 | kl: 1.2347 + pw: 1258.7024 = loss: 1259.9371 | KL v02
Epoch: 001/180 | Batch 540/1769 | kl: 3.2154 + pw: 1294.9265 = loss: 1298.1420 | KL v02
Epoch: 001/180 | Batch 720/1769 | kl: 2.8175 + pw: 1296.5161 = loss: 1299.3336 | KL v02
Epoch: 001/180 | Batch 900/1769 | kl: 4.6099 + pw: 1287.4602 = loss: 1292.0702 | KL v02
Epoch: 001/180 | Batch 1080/1769 | kl: 4.6800 + pw: 1509.1508 = loss: 1513.8308 | KL v02
Epoch: 001/180 | Batch 1260/1769 | kl: 27.6977 + pw: 1004.7749 = loss: 1032.4727 | KL v02
Epoch: 001/180 | Batch 1440/1769 | kl: 26.7823 + pw: 1047.0830 = loss: 1073.8652 | KL v02
Epoch: 001/180 | Batch 1620/1769 | kl: 4.4410 + pw: 1229.0769 = loss: 1233.5178 | KL v02
Time elapsed: 0.09 min
Epoch: 002/180 | Batch 000/1769 | kl: 4.2533 + pw: 1257.4656 = loss: 1261.71